#Set Connection to ADLS

In [0]:
#Connect to ADLS
spark.conf.set('fs.azure.account.key.yelpprojectstorage.dfs.core.windows.net', 'SxK5rbjNin+OUDsfA0YH7fVkDU2iIpKcZZ5FxIviKKasbb9bBKOUTR2QyXOAe67D67F5wjJiI6m7+ASteMd5PA==')

In [0]:
#List datasets
dbutils.fs.ls("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/")

Out[6]: [FileInfo(path='abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_business.json', name='yelp_academic_dataset_business.json', size=118863795, modificationTime=1658778924000),
 FileInfo(path='abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_checkin.json', name='yelp_academic_dataset_checkin.json', size=286958945, modificationTime=1658778922000),
 FileInfo(path='abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_review.json', name='yelp_academic_dataset_review.json', size=5341868833, modificationTime=1658778956000),
 FileInfo(path='abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_tip.json', name='yelp_academic_dataset_tip.json', size=180604475, modificationTime=1658778925000),
 FileInfo(path='abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_user.json', name='yelp_academic_dataset_user.json', size=3363329011, modificationTime=1658778948000)]

In [0]:
#Convert to parquet in new folder
new_path = "abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/parquet_files/"
suffix = '.parquet'
for path in dbutils.fs.ls("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/"):
    file = path.path[82:]
    file = file[:-5]
    write_path = new_path + file + suffix
    df = spark.read.json(path.path)
    df.write.mode('overwrite').parquet(write_path)

In [0]:
#Convert to Delta Files
new_path = "abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_delta_files/"
suffix = '.delta'
for path in dbutils.fs.ls("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/"):
    if path.path[-4:] == 'json':
        file = path.path[82:]
        file = file[:-5]
        write_path = new_path + file + suffix
        df = spark.read.json(path.path)
        df.write.format("delta").mode("overwrite").save(write_path)
    else:
        continue

abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_business.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_business.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_checkin.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_checkin.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_review.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_review.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_tip.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_tip.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_user.json
abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_user.json

#Load in delta dataframes for analysis
###Practice Repartitions & Coalesce

In [0]:
#Confirm same row count across file types
business_df = spark.read.format("delta").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_delta_files/business.delta")
print(business_df.count())
business_df = spark.read.format("parquet").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/parquet_files/business.parquet")
print(business_df.count())
business_df = spark.read.format("json").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_academic_dataset_business.json")
print(business_df.count())


150346
150346
150346

In [0]:
#Load in dataframes 
business_df = spark.read.format("delta").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_delta_files/business.delta")
checkin_df = spark.read.format("delta").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_delta_files/checkin.delta")
review_df = spark.read.format("delta").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_delta_files/review.delta")
tip_df = spark.read.format("delta").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_delta_files/tip.delta")
user_df = spark.read.format("delta").load("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/yelp_delta_files/user.delta")

print('business df: ', business_df.count())
print('checkin df: ', checkin_df.count())
print('review df: ', review_df.count())
print('tip df: ', tip_df.count())
print('user df: ', user_df.count())

business df: 150346
checkin df: 131930
review df: 6990280
tip df: 908915
user df: 1987897

In [0]:
display(review_df)

business_id cool date funny review_id stars text useful user_id XQfwVwDr-v0ZS3_CbbE5Xw 0 2018-07-07 22:09:11 0 KU_O5udG6zpxOg-VcAEodg 3.0 If you decide to eat here, just be aware it is going to take about 2 hours from beginning to end. We have tried it multiple times, because I want to like it! I have been to it's other locations in NJ and never had a bad experience. 

The food is good, but it takes a very long time to come out. The waitstaff is very young, but usually pleasant. We have just had too many experiences where we spent way too long waiting. We usually opt for another diner or restaurant on the weekends, in order to be done quicker. 0 mh_-eMZ6K5RLWhZyISBhwA 7ATYjTIgM3jUlt4UM3IypQ 1 2012-01-03 15:28:18 0 BiTunyQ73aT9WBnpR9DZGw 5.0 I've taken a lot of spin classes over the years, and nothing compares to the classes at Body Cycle. From the nice, clean space and amazing bikes, to the welcoming and motivating instructors, every class is a top notch work out.

For anyone who struggles to fit workouts in, the online scheduling system makes it easy to plan ahead (and there's no need to line up way in advanced like many gyms make you do).

There is no way I can write this review without giving Russell, the owner of Body Cycle, a shout out. Russell's passion for fitness and cycling is so evident, as is his desire for all of his clients to succeed. He is always dropping in to classes to check in/provide encouragement, and is open to ideas and recommendations from anyone. Russell always wears a smile on his face, even when he's kicking your butt in class! 1 OyoGAe7OKpv6SyGZT5g77Q YjUWPpI6HXG530lwP-fb2A 0 2014-02-05 20:30:30 0 saUsX_uimxRlCVr67Z4Jig 3.0 Family diner. Had the buffet. Eclectic assortment: a large chicken leg, fried jalapeño, tamale, two rolled grape leaves, fresh melon. All good. Lots of Mexican choices there. Also has a menu with breakfast served all day long. Friendly, attentive staff. Good place for a casual relaxed meal with no expectations. Next to the Clarion Hotel. 0 8g_iMtfSiwikVnbP2etR0A kxX2SOes4o-D3ZQBkiMRfA 1 2015-01-04 00:01:03 0 AqPFMleE6RsU23_auESxiA 5.0 Wow! Yummy, different, delicious. Our favorite is the lamb curry and korma. With 10 different kinds of naan!!! Don't let the outside deter you (because we almost changed our minds)...go in and try something new! You'll be glad you did! 1 _7bHUi9Uuf5__HHc_Q8guQ e4Vwtrqf-wpJfwesgvdgxQ 1 2017-01-14 20:54:15 0 Sx8TMOWLNuJBWer-0pcmoA 4.0 Cute interior and owner (?) gave us tour of upcoming patio/rooftop area which will be great on beautiful days like today. Cheese curds were very good and very filling. Really like that sandwiches come w salad, esp after eating too many curds! Had the onion, gruyere, tomato sandwich. Wasn't too much cheese which I liked. Needed something else...pepper jelly maybe. Would like to see more menu options added such as salads w fun cheeses. Lots of beer and wine as well as limited cocktails. Next time I will try one of the draft wines. 1 bcjbaE6dDog4jkNY91ncLQ 04UD14gamNjLY0IDYVhHJg 1 2015-09-23 23:10:31 2 JrIxlS1TzJ-iCu79ul40cQ 1.0 I am a long term frequent customer of this establishment. I just went in to order take out (3 apps) and was told they're too busy to do it. Really? The place is maybe half full at best. Does your dick reach your ass? Yes? Go fuck yourself! I'm a frequent customer AND great tipper. Glad that Kanella just opened. NEVER going back to dmitris! 1 eUta8W_HdHMXPzLBBZhL1A gmjsEdUsKpj9Xxu6pdjH0g 0 2015-01-03 23:21:18 2 6AxgBCNX_PNTOxmbRSwcKQ 5.0 Loved this tour! I grabbed a groupon and the price was great. It was the perfect way to explore New Orleans for someone who'd never been there before and didn't know a lot about the history of the city. Our tour guide had tons of interesting tidbits about the city, and I really enjoyed the experience. Highly recommended tour. I actually thought we were just going to tour through the cemetery, but she took us around the French Quarter for the first hour, and the cemet

In [0]:
#Extract month, year 
from pyspark.sql import functions as f
review_df = review_df.withColumn('Year', f.year(review_df.date))
review_df = review_df.withColumn('Month', f.month(f.col('date')))

In [0]:
display(review_df)

business_id cool date funny review_id stars text useful user_id Year Month XQfwVwDr-v0ZS3_CbbE5Xw 0 2018-07-07 22:09:11 0 KU_O5udG6zpxOg-VcAEodg 3.0 If you decide to eat here, just be aware it is going to take about 2 hours from beginning to end. We have tried it multiple times, because I want to like it! I have been to it's other locations in NJ and never had a bad experience. 

The food is good, but it takes a very long time to come out. The waitstaff is very young, but usually pleasant. We have just had too many experiences where we spent way too long waiting. We usually opt for another diner or restaurant on the weekends, in order to be done quicker. 0 mh_-eMZ6K5RLWhZyISBhwA 2018 7 7ATYjTIgM3jUlt4UM3IypQ 1 2012-01-03 15:28:18 0 BiTunyQ73aT9WBnpR9DZGw 5.0 I've taken a lot of spin classes over the years, and nothing compares to the classes at Body Cycle. From the nice, clean space and amazing bikes, to the welcoming and motivating instructors, every class is a top notch work out.

For anyone who struggles to fit workouts in, the online scheduling system makes it easy to plan ahead (and there's no need to line up way in advanced like many gyms make you do).

There is no way I can write this review without giving Russell, the owner of Body Cycle, a shout out. Russell's passion for fitness and cycling is so evident, as is his desire for all of his clients to succeed. He is always dropping in to classes to check in/provide encouragement, and is open to ideas and recommendations from anyone. Russell always wears a smile on his face, even when he's kicking your butt in class! 1 OyoGAe7OKpv6SyGZT5g77Q 2012 1 YjUWPpI6HXG530lwP-fb2A 0 2014-02-05 20:30:30 0 saUsX_uimxRlCVr67Z4Jig 3.0 Family diner. Had the buffet. Eclectic assortment: a large chicken leg, fried jalapeño, tamale, two rolled grape leaves, fresh melon. All good. Lots of Mexican choices there. Also has a menu with breakfast served all day long. Friendly, attentive staff. Good place for a casual relaxed meal with no expectations. Next to the Clarion Hotel. 0 8g_iMtfSiwikVnbP2etR0A 2014 2 kxX2SOes4o-D3ZQBkiMRfA 1 2015-01-04 00:01:03 0 AqPFMleE6RsU23_auESxiA 5.0 Wow! Yummy, different, delicious. Our favorite is the lamb curry and korma. With 10 different kinds of naan!!! Don't let the outside deter you (because we almost changed our minds)...go in and try something new! You'll be glad you did! 1 _7bHUi9Uuf5__HHc_Q8guQ 2015 1 e4Vwtrqf-wpJfwesgvdgxQ 1 2017-01-14 20:54:15 0 Sx8TMOWLNuJBWer-0pcmoA 4.0 Cute interior and owner (?) gave us tour of upcoming patio/rooftop area which will be great on beautiful days like today. Cheese curds were very good and very filling. Really like that sandwiches come w salad, esp after eating too many curds! Had the onion, gruyere, tomato sandwich. Wasn't too much cheese which I liked. Needed something else...pepper jelly maybe. Would like to see more menu options added such as salads w fun cheeses. Lots of beer and wine as well as limited cocktails. Next time I will try one of the draft wines. 1 bcjbaE6dDog4jkNY91ncLQ 2017 1 04UD14gamNjLY0IDYVhHJg 1 2015-09-23 23:10:31 2 JrIxlS1TzJ-iCu79ul40cQ 1.0 I am a long term frequent customer of this establishment. I just went in to order take out (3 apps) and was told they're too busy to do it. Really? The place is maybe half full at best. Does your dick reach your ass? Yes? Go fuck yourself! I'm a frequent customer AND great tipper. Glad that Kanella just opened. NEVER going back to dmitris! 1 eUta8W_HdHMXPzLBBZhL1A 2015 9 gmjsEdUsKpj9Xxu6pdjH0g 0 2015-01-03 23:21:18 2 6AxgBCNX_PNTOxmbRSwcKQ 5.0 Loved this tour! I grabbed a groupon and the price was great. It was the perfect way to explore New Orleans for someone who'd never been there before and didn't know a lot about the history of the city. Our tour guide had tons of interesting tidbits about the city, and I really enjoyed the experience. Highly recommended tour. I actually thought we were just going to tour through the cemetery, but she took us around

In [0]:
#Export review_df partitioned by year then month
review_df.write.mode('overwrite').partitionBy('Year', 'Month').parquet("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/reviews_partitioned_by_year_month/")

In [0]:
#Investigate number of partitions (Storage account says 25)
user_df.rdd.getNumPartitions()
#Matches

Out[54]: 25

In [0]:
#Current Partitions uneven, try Coalesce and Repartition methods on user
#reduce with coalesce
user_reduced_c = user_df.coalesce(10)
print('Coalesce:', user_reduced_c.rdd.getNumPartitions())

user_reduced_r = user_df.repartition(10)
print('Repartitioned:', user_reduced_c.rdd.getNumPartitions())

Coalesce: 10
Repartitioned: 10

In [0]:
#Inspect raw files in container
user_reduced_c.write.parquet("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/coalesce/")
user_reduced_r.write.parquet("abfss://yelp-target@yelpprojectstorage.dfs.core.windows.net/repartition/")

#Answering Business Questions

In [0]:
#Allow sql to work w spark dataframe
user_df.createOrReplaceTempView("user")

In [0]:
%sql
--Top 10 users with most fans
SELECT user_id, fans 
FROM user
ORDER BY fans DESC
limit 10;

user_id fans 37cpUoM8hlkSQfReIEBd-Q 12497 hizGc5W1tBHPghM5YKCAtg 3642 Hi10sGSZNxQH3NLyWSZ1oA 3493 JjXuiru1_ONzDkYVrHN0aw 3243 j14WgRoU_-2ZE1aw1dXrJg 3138 VHdY6oG2JPVNjihWhOooAQ 2627 iLjMdZi0Tm7DQxX1C1_2dg 2547 lt7bNHl-TXziny4FETu8nA 2451 fgwI3rYHOv1ipfVfCSx7pg 2424 ITa3vh5ERI90G_WP4SmGUQ 2388

In [0]:
%sql
--Order by most reviews
SELECT name, user_id, review_count
FROM user
ORDER BY review_count DESC
LIMIT 3;

name user_id review_count Fox Hi10sGSZNxQH3NLyWSZ1oA 17473 Victor 8k3aO-mPeyhbR5HUucA5aA 16978 Bruce hWDybu_KvYLSdEFzGrniTw 16567

In [0]:
#Top 10 categories #not counting same place as several reviews; just 1
from pyspark.sql.window import Window
cat_count = business_df.groupBy('categories').agg(f.count(business_df.review_count).alias('reviews'))
cat_count = cat_count.withColumn('rank',f.row_number().over(Window.orderBy(f.col('reviews').desc())))
cat_count = cat_count.filter("rank <= 10")
display(cat_count)

categories reviews rank Beauty & Spas, Nail Salons 1012 1 Restaurants, Pizza 935 2 Nail Salons, Beauty & Spas 934 3 Pizza, Restaurants 823 4 Restaurants, Mexican 728 5 Restaurants, Chinese 708 6 Mexican, Restaurants 672 7 Chinese, Restaurants 651 8 Food, Coffee & Tea 508 9 Beauty & Spas, Hair Salons 493 10

In [0]:
business_df.createOrReplaceTempView('business')

In [0]:
%sql
SELECT categories, COUNT(review_count)
FROM business
GROUP BY 1
ORDER BY 2 DESC
LIMIT 10;

categories count(review_count) Beauty & Spas, Nail Salons 1012 Restaurants, Pizza 935 Nail Salons, Beauty & Spas 934 Pizza, Restaurants 823 Restaurants, Mexican 728 Restaurants, Chinese 708 Mexican, Restaurants 672 Chinese, Restaurants 651 Food, Coffee & Tea 508 Beauty & Spas, Hair Salons 493

In [0]:
#Categories with more than 1000 reviews
cat_count = business_df.groupBy('categories').agg(f.count('review_count').alias('reviews'))
cat_count = cat_count.withColumn('rank', f.row_number().over(Window.orderBy(f.col('reviews').desc())))
cat_count.show()

+--------------------+-------+----+
 categories|reviews|rank|
+--------------------+-------+----+
Beauty & Spas, Na...| 1012| 1|
 Restaurants, Pizza| 935| 2|
Nail Salons, Beau...| 934| 3|
 Pizza, Restaurants| 823| 4|
Restaurants, Mexican| 728| 5|
Restaurants, Chinese| 708| 6|
Mexican, Restaurants| 672| 7|
Chinese, Restaurants| 651| 8|
 Food, Coffee & Tea| 508| 9|
Beauty & Spas, Ha...| 493| 10|
Hair Salons, Beau...| 480| 11|
 Coffee & Tea, Food| 473| 12|
Automotive, Auto ...| 361| 13|
Auto Repair, Auto...| 351| 14|
 Grocery, Food| 329| 15|
Italian, Restaurants| 328| 16|
 Food, Grocery| 306| 17|
 Veterinarians, Pets| 300| 18|
Ice Cream & Froze...| 298| 19|
 Pets, Veterinarians| 285| 20|
+--------------------+-------+----+
only showing top 20 rows

In [0]:
#Number of Restaurants per State
states = business_df.groupBy('State').agg(f.count('name').alias('Restaurants')).orderBy('Restaurants', ascending=False)
display(states)

State Restaurants PA 34039 FL 26330 TN 12056 IN 11247 MO 10913 LA 9924 AZ 9912 NJ 8536 NV 7715 AB 5573 CA 5203 ID 4467 DE 2265 IL 2145 TX 4 CO 3 MA 2 WA 2 HI 2 MI 1 MT 1 NC 1 XMS 1 UT 1 SD 1 VT 1 VI 1

150346
150346

In [0]:
#Top 3 Restaurants by State, review count
business_df.createOrReplaceTempView('restaurants')

In [0]:
%sql
SELECT *
FROM (SELECT state, name, review_count,
      ROW_NUMBER() OVER (PARTITION BY state ORDER BY review_count DESC) as rank
      FROM restaurants)
WHERE rank <= 3;

state name review_count rank AZ Prep & Pastry 2126 1 AZ El Charro Cafe 1583 2 AZ Cafe Poca Cosa 1306 3 LA Acme Oyster House 7568 1 LA Oceana Grill 7400 2 LA Ruby Slipper - New Orleans 5193 3 MI Mr Brakes 9 1 NJ The Farm and Fisherman Tavern 709 1 NJ Dolsot House 665 2 NJ The Jug Handle Inn 604 3 NV Grand Sierra Resort and Casino 3345 1 NV Peg's Glorified Ham N Eggs 2506 2 NV Peppermill Reno 2486 3 CA Los Agaves 3834 1 CA Brophy Bros - Santa Barbara 2940 2 CA Boathouse at Hendry's Beach 2536 3 DE Border Cafe 742 1 DE Iron Hill Brewery & Restaurant 512 2 DE Big Fish Grill - Riverfront 456 3 ID Fork 1810 1 ID Barbacoa Grill 1099 2 ID Bittercreek Alehouse 998 3 IL BEAST Craft BBQ 583 1 IL Lotawata Creek Southern Grill 550 2 IL Cleveland-Heath 455 3 IN The Eagle 2233 1 IN St. Elmo Steak House 2035 2 IN Bakersfield 1642 3 MO Pappy's Smokehouse 3999 1 MO Broadway Oyster Bar 2076 2 MO Rooster - Downtown 1984 3 MT MudMan Food Truck 6 1 NC IHOP 29 1 VI The Moorings 10 1 VT All Service Citgo 10 1 WA Valvoline Instant Oil Change 13 1 WA Suave Nails 6 2 XMS Pumpernickles Catering 5 1 AB Duchess Bake Shop 486 1 AB SugarBowl 435 2 AB Tres Carnales Taqueria 429 3 CO Two Elk Restaurant 12 1 CO Breeze Ski Rentals 10 2 CO Travis Darnell Photography 8 3 FL Datz 3260 1 FL Ulele 3064 2 FL Bern's Steak House 2924 3 HI Cosmetic Solutions 17 1 HI 2 Sisters Photography 15 2 MA United Parcel Service 34 1 MA YOCO Maids & Cleaning 9 2 PA Reading Terminal Market 5721 1 PA Pat's King of Steaks 4250 2 PA Geno's Steaks 3401 3 SD K Soho Salon 42 1 TN Hattie B’s Hot Chicken - Nashville 6093 1 TN Biscuit Love: Gulch 4207 2 TN The Pharmacy 3054 3 TX 2400 Briarwest 12 1 TX Wildlife Wonders 9 2 TX Southern Luxe Beauty 7 3 UT Find Your Zen 19 1

In [0]:
#List top restaurants in Arizona by reviews
arizona = business_df.filter("state == 'AZ'")
arizona = arizona.groupBy('name').agg(f.count('review_count').alias('reviews'))
arizona = arizona.withColumn('rank', f.row_number().over(Window.orderBy(f.desc('reviews'))))
arizona = arizona.select('name', 'rank', 'reviews')
display(arizona)

name rank reviews Starbucks 1 63 Subway 2 50 Walgreens 3 44 McDonald's 4 41 eegee's 5 27 The UPS Store 6 26 Circle K 7 24 Burger King 8 23 Taco Bell 9 22 Supercuts 10 21 Domino's Pizza 11 20 QuikTrip 12 20 Panda Express 13 20 CVS Pharmacy 14 20 Jack in the Box 15 19 Ace Hardware 16 19 Pizza Hut 17 17 Dairy Queen 18 17 Safeway 19 16 Mister Car Wash 20 16 Chipotle Mexican Grill 21 15 T-Mobile 22 15 BRAKEmax 23 15 US Post Office 24 14 Jiffy Lube 25 14 Goodwill Thrift Store and Donation Center 26 14 Wendy's 27 14 Brake Masters 28 14 AutoZone Auto Parts 29 13 Great Clips 30 13 O'Reilly Auto Parts 31 13 Nationwide Vision Centers 32 13 Wells Fargo Bank 33 13 Bank of America Financial Center 34 13 Dutch Bros Coffee 35 13 Cost Cutters 36 13 Little Caesars Pizza 37 12 Denny's 38 12 Ross Dress for Less 39 12 Carl's Jr 40 12 Enterprise Rent-A-Car 41 12 Papa John's Pizza 42 12 Discount Tire 43 12 AT&T Store 44 11 Bruegger's Bagels 45 11 Chase Bank 46 11 Arby's 47 11 Petco 48 10 Walmart Supercenter 49 10 KFC 50 10 Dunkin' 51 10 Walmart Neighborhood Market 52 10 Jimmy John's 53 10 Firestone Complete Auto Care 54 10 Papa Murphy's 55 10 Peter Piper Pizza 56 9 Fry's Food & Drug Stores 57 9 Southern Arizona Urgent Care 58 9 Leslie's 59 9 Baggin's Gourmet Sandwiches 60 9 PetSmart 61 9 Los Betos 62 9 Viva Burrito 63 8 Sonic Drive-In 64 8 Verizon 65 8 Target 66 8 NextCare Urgent Care 67 8 Jersey Mike's Subs 68 8 Sonora Quest Laboratories 69 7 Albertsons 70 7 In-N-Out Burger 71 7 Church's Chicken 72 7 Midas 73 7 Mariscos Chihuahua 74 7 MOD Pizza 75 7 Wienerschnitzel 76 7 CubeSmart Self Storage 77 7 Jerry Bob's Family Restaurant 78 7 Public Storage 79 7 Whataburger 80 7 Lucky Wishbone 81 7 Popeyes Louisiana Kitchen 82 7 Anytime Fitness 83 6 Sally Beauty Supply 84 6 Culver's 85 6 The Home Depot 86 6 El Charro Cafe 87 6 LA Fitness 88 6 Famous Sam's 89 6 Pima Federal Credit Union 90 6 Wingstop 91 6 Style America 92 6 Cold Stone Creamery 93 6 IHOP 94 6 Chick-fil-A 95 6 Food City 96 6 Gamestop 97 6 Pep Boys 98 6 First Watch 99 6 Jack Furrier Tire & Auto Care 100 6 Hughes Federal Credit Union 101 6 Sprouts Farmers Market 102 6 Five Guys 103 6 Walmart 104 5 Vantage West Credit Union 105 5 Taco Giro 106 5 Magpies Gourmet Pizza 107 5 Serial Grillers 108 5 FedEx Office Print & Ship Center 109 5 Truly Nolen Pest & Termite Control 110 5 Dollar Tree Store 111 5 Planet Fitness 112 5 Waffle House 113 5 Native Grill & Wings 114 5 Banner Urgent Care 115 5 Officemax 116 5 ProActive Physical Therapy 117 5 Tucson Federal Credit Union 118 5 Goodyear Auto Service Center 119 5 Panera Bread 120 5 Sprint Store 121 5 Shaffer Dry Cleaning & Laundry 122 5 Big Lots 123 5 Banfield Pet Hospital 124 5 Nico's Taco Shop 125 4 Pyramid Federal Credit Union 126 4 Smashburger 127 4 Surf Thru Express Car Wash 128 4 Bath & Body Works 129 4 Village Inn 130 4 First Chiropractic 131 4 Moon Smoke Shop 132 4 Beyond Bread 133 4 Smoothie King 134 4 7-Eleven 135 4 Chuy's Mesquite Broiler 136 4 Einstein Bros. Bagels 137 4 Bisbee Breakfast Club 138 4 Octopus Car Wash 139 4 Hertz Rent A Car 140 4 ChickeNuevo 141 4 Chili's 142 4 Batteries Plus Bulbs 143 4 Tucson Cleaners 144 4 Los Betos Mexican Food 145 4 Freedom Smoke USA 146 4 Play It Again Sports 147 4 Natural Grocers 148 4 Precious Metals Refinery 149 4 Baskin-Robbins 150 4 Headliners Barber Shop 151 4 America's Best Contacts & Eyeglasses 152 4 Rubio's 153 4 The Pet Club 154 4 Donut Wheel 155 4 Labcorp 156 4 Chuze Fitness 157 4 Motel 6 158 4 Big O Tire Stores 159 4 Boston Market 160 4 Olive Garden Italian Restaurant 161 4 Sauce Pizza & Wine 162 4 Arizona Auto Spa 163 4 The Joint Chiropractic 164 4 Alvernon Optical 165 4 Lowe's Home Improvement 166 4 Platinum Fitness 167 4 Verizon Authorized Retailer, TCC 168 4 Michaels 169 4 Northwest Allied Physicians 170 4 Ulta Beauty 171 4 Hungry Howie's Pizza 172 4 99 Cents Only Stores 173 4 Red Lobster 174 4 Trader Joe's 175 4 Freddy's Frozen Custard & Steakburgers 176 4 Brooklyn Bedding 177 4 Fito's Taco Sho

In [0]:
#Restaurant count by state and city
state_city = business_df.groupBy("state", "city").count().orderBy(f.desc('count'))

display(state_city.filter("state == 'AZ'"))

state city count AZ Tucson 9249 AZ Oro Valley 286 AZ Marana 102 AZ Green Valley 69 AZ Sahuarita 69 AZ Vail 51 AZ Tuscon 18 AZ Catalina 13 AZ Mount Lemmon 7 AZ TUCSON 6 AZ Casas Adobes 4 AZ tucson 4 AZ South Tucson 3 AZ Cortaro 3 AZ Corona de Tucson 3 AZ Tucson, Arizona 2 AZ Corona De Tucson 2 AZ Catalina Foothills 2 AZ Oracle 2 AZ Rillito 2 AZ Tucson 2 AZ Santa Rita 1 AZ Picture Rocks 1 AZ Los Ranchitos 1 AZ Green Valle 1 AZ Drexel Heights 1 AZ Summerhaven 1 AZ Maran 1 AZ Oro valley 1 AZ Tuson 1 AZ Arizona 1 AZ TUCSON AP 1 AZ Valencia West 1 AZ Casa Adobes 1

In [0]:
#City with most
top_city = state_city.filter("city == 'Tucson' and state == 'AZ'")
print(type(top_city))
display(top_city)

<class 'pyspark.sql.dataframe.DataFrame'>

state city count AZ Tucson 9249

In [0]:
#Broadcast Join
#Smaller df so it's available in memory no shuffling during join (bc of partitions)
from pyspark.sql.functions import broadcast
#df top city + df business
new_df = business_df.join(broadcast(top_city), on='city', how='inner')
display(new_df)

city address attributes business_id categories hours is_open latitude longitude name postal_code review_count stars state state count Tucson 8581 N Silverbell Rd List(null, null, u'none', {'touristy': False, 'hipster': False, 'romantic': False, 'divey': False, 'intimate': False, 'trendy': False, 'upscale': False, 'classy': False, 'casual': False}, False, null, null, True, null, True, {'garage': False, 'street': False, 'validated': False, 'lot': False, 'valet': False}, null, False, null, null, null, False, null, null, True, {'dessert': False, 'latenight': False, 'lunch': False, 'dinner': False, 'brunch': False, 'breakfast': False}, null, null, True, null, u'average', null, False, null, null, True, True, 1, True, True, True, null, True, 'free') 2tAi411srrpmMofeAKdACw Coffee & Tea, Breakfast & Brunch, Food, Restaurants List(6:30-12:0, 0:0-0:0, 6:30-12:30, 6:30-12:30, 6:30-12:0, 6:30-12:0, 6:30-12:0) 1 32.362689 -111.120753 Just Breakfast on Silverbell 85743 113 3.5 AZ AZ 9249 Tucson 3655 N Oracle Rd, Ste 101 List(null, null, null, null, null, null, null, null, null, True, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null) kdZr-IdMNOUNZxbZDy8TeQ Public Services & Government, Local Services, Shipping Centers, Post Offices List(10:0-17:0, 10:0-17:0, null, null, 10:0-17:0, 10:0-17:0, 10:0-17:0) 1 32.273139 -110.9790247 US Post Office 85705 11 1.5 AZ AZ 9249 Tucson 2110 W Brichta Dr List(null, null, null, null, null, null, null, null, null, True, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null) qE6PBhgB7AFtUHTp0nh9zA Local Services, Preschools, Child Care & Day Care, Education List(6:0-18:0, 6:0-18:0, null, null, 6:0-18:0, 6:0-18:0, 6:0-18:0) 1 32.24167 -111.012518 Brichta Infant and Early Learning Child Care Center 85745 17 4.5 AZ AZ 9249 Tucson 245 E Congress St List(null, null, null, null, null, null, null, True, False, True, {'garage': True, 'street': True, 'validated': False, 'lot': False, 'valet': False}, null, True, null, null, null, True, False, null, True, null, null, null, null, null, u'average', null, null, null, null, None, null, 1, null, null, True, null, True, 'no') JkQz12i_Eubd_xQdLLkDxQ Restaurants, Food, Juice Bars & Smoothies, Ice Cream & Frozen Yogurt List(12:0-22:0, 12:0-21:0, 12:0-22:0, 12:0-21:0, 12:0-21:0, 12:0-21:0, 12:0-21:0) 1 32.2221884 -110.9673208 HUB Ice Cream Factory 85701 181 4.0 AZ AZ 9249 Tucson 315 N 4th Ave List(null, null, null, null, null, null, null, True, False, True, {'garage': False, 'street': True, 'validated': False, 'lot': False, 'valet': False}, False, null, null, null, null, null, null, null, null, null, null, null, null, null, u'average', null, null, null, null, null, null, 2, null, null, null, null, True, u'no') C32fy017b5exHYo6x4zQfQ Beauty & Spas, Arts & Entertainment, Permanent Makeup, Professional Services, Piercing, Graphic Design, Tattoo, Shopping, Art Galleries List(12:0-2:0, 0:0-0:0, 12:0-2:0, 12:0-0:0, 12:0-0:0, 12:0-0:0, 12:0-0:0) 1 32.2255671 -110.9658392 Sacred Art Tattoo Studio 85705 77 3.5 AZ AZ 9249 Tucson 2707 E Broadway Blvd List(null, null, 'beer_and_wine', {'touristy': False, 'hipster': False, 'romantic': False, 'divey': None, 'intimate': False, 'trendy': False, 'upscale': False, 'classy': False, 'casual': True}, null, 'yes_free', null, True, null, True, {'garage': False, 'street': False, 'validated': False, 'lot': True, 'valet': False}, null, True, null, False, null, False, null, null, True, {'dessert': False, 'latenight': False, 'lunch': True, 'dinner': True, 'brunch': False, 'breakfast': False}, null, True, True, null, u'average', null, True, 'casual', null, True, True, 2, False, True, True, null, null, u'no') 9zlIJ7Q5W4AENjpGgaNSsQ Chicken Wings, Restaurants, Pizza, Sandwiches List(11:0-22:0, 11:0-22:0, 11:0-22:0, 11:0-2

In [0]:
#Most Reviewed Italian Restaurant
italian_df = business_df.filter("LOWER(categories) LIKE '%italian%'")
#display(italian_df.select('name', 'review_count', 'categories').orderBy(f.desc('review_count')))
display(italian_df.select('name', 'review_count', 'categories').orderBy('review_count', ascending=False).take(10))

name review_count categories Pat's King of Steaks 4250 Italian, American (Traditional), Sandwiches, Fast Food, Restaurants, Local Flavor, Cheesesteaks Barbuzzo 2893 Mediterranean, Restaurants, Pizza, Italian Jim's South St 2736 Bars, Restaurants, Pizza, Cheesesteaks, Italian, Beer Bar, American (Traditional), Local Flavor, Nightlife, Sandwiches Domenica 1906 Restaurants, Italian, Pizza, Tapas/Small Plates Mazzaro's Italian Market 1551 Specialty Food, Delis, Coffee Roasteries, Butcher, Meat Shops, Food, Restaurants, Grocery, Italian Five Points Pizza 1293 Nightlife, Bars, Italian, Restaurants, Pizza, Food Noble Crust 1259 Breakfast & Brunch, Pizza, Southern, Italian, Nightlife, Bars, Restaurants, American (Traditional) Mixto 1246 Latin American, Argentine, Restaurants, Breakfast & Brunch, Italian, Cuban, Caribbean Campo 1164 Italian, Restaurants Little Nonna's 1147 Restaurants, Italian